In [12]:
import numpy as np
import matplotlib.pyplot as plt
# import axes3d for 3D plotting
from mpl_toolkits.mplot3d import Axes3D

np.set_printoptions(precision=8, suppress=True)



In [13]:
# load data

displacement = np.load('../npy/2024-04-24_16:14:43/train/CoarseResPoints.npy')

hr_displacement = np.load('../npy/2024-04-24_16:14:43/train/HighResPoints.npy')

print(displacement.shape)
print(hr_displacement.shape)

(119, 250, 3)
(119, 1000, 3)


In [14]:
displacement = displacement.reshape((displacement.shape[0], 10, 25, 3))
print(displacement.shape)
hr_displacement = hr_displacement.reshape((hr_displacement.shape[0], 20, 50, 3))
print(hr_displacement.shape)

(119, 10, 25, 3)
(119, 20, 50, 3)


In [15]:
# print the first 5 values of the displacement and position

print(displacement)
print(hr_displacement[:1])



[[[[ 0.          0.          0.        ]
   [ 0.00558814  0.00368027  0.        ]
   [ 0.01033437  0.0080222   0.        ]
   ...
   [ 0.04034244  0.30599454  0.        ]
   [ 0.03997854  0.32442535  0.        ]
   [ 0.03959196  0.34284084  0.        ]]

  [[ 0.          0.          0.        ]
   [ 0.00381308  0.00270206  0.        ]
   [ 0.00773525  0.00712435  0.        ]
   ...
   [ 0.03052415  0.30576004  0.        ]
   [ 0.03016145  0.32419877  0.        ]
   [ 0.02977495  0.34261337  0.        ]]

  [[ 0.          0.          0.        ]
   [ 0.00257443  0.00210732  0.        ]
   [ 0.00538329  0.0064075   0.        ]
   ...
   [ 0.02072934  0.30552675  0.        ]
   [ 0.02036076  0.32397159  0.        ]
   [ 0.01997245  0.34238312  0.        ]]

  ...

  [[ 0.          0.          0.        ]
   [-0.00232974  0.00198849  0.        ]
   [-0.0047905   0.00610151  0.        ]
   ...
   [-0.0281241   0.30443086  0.        ]
   [-0.02854801  0.32288051  0.        ]
   [-0.02896089 

In [16]:

# boundary_points_dir = []
# for i in range(hr_displacement.shape[0]):
#     if hr_displacement[i,0] == 0.:
#         boundary_points_dir.append(i)

# print(boundary_points_dir)
# print(len(boundary_points_dir))

# boundary_points_neu = []
# for i in range(hr_displacement.shape[0]):
#     if hr_displacement[i,0] == 10.:
#         boundary_points_neu.append(i)

# print(boundary_points_neu)
# print(len(boundary_points_neu))

In [17]:
# # same plot using vedo window

# import vedo
# vedo.settings.default_backend = 'vtk'

# # create a mesh object
# mesh_rest = vedo.Points(position, r=5, c='r')
# # reco_rest = mesh_rest.reconstruct_surface()

# mesh = vedo.Points(position + displacement, r=5)
# # reco = mesh.reconstruct_surface()

# # show the mesh
# if show_mesh:
#     vedo.show(mesh, mesh_rest, axes=1, viewup='z')

#     vedo.close()



In [18]:

def pooling_3D(displacement, low_resh_shape=None):
    if low_resh_shape is None:
        low_resh_shape = displacement.shape[1]//2, displacement.shape[2]//2, displacement.shape[3]
    y, x, z = low_resh_shape
    pool = np.zeros((displacement.shape[0], y, x, z))

    for i in range(displacement.shape[0]):
        for j in range(y):
            for k in range(x):
                # check if the point is on the boundary
                if k == 0:
                    pool[i, j, k] = displacement[i, 2*j, 2*k]
                else:
                    # this must be fixed since it assumes that the pooling kernel is 2x2 and i'm not that a good computer scientist but works on my toy example
                    print(displacement[i, 2*j:2*j+2, 2*k:2*k+2])
                    pool[i, j, k] = np.mean(displacement[i, 2*j:2*j+2, 2*k:2*k+2], axis=(0, 1))
    
    return pool



In [19]:
pooled = pooling_3D(hr_displacement, low_resh_shape=displacement.shape[1:])
print(pooled.shape)

# get count of nan values in the pooled displacement

print(np.count_nonzero(np.isnan(pooled)))

# print the first 5 values of the pooled displacement and position
print(pooled[0, :1])
print(displacement[0, :1])

print(pooled[5, :1] - displacement[5, :1])


[[[0.00567479 0.00383848 0.        ]
  [0.00810905 0.00577776 0.        ]]

 [[0.00479807 0.00334688 0.        ]
  [0.00705405 0.005303   0.        ]]]
[[[0.01046437 0.00810367 0.        ]
  [0.01273675 0.01085222 0.        ]]

 [[0.00920355 0.00764197 0.        ]
  [0.01126183 0.01040394 0.        ]]]
[[[0.0149167  0.01402567 0.        ]
  [0.01699884 0.01761333 0.        ]]

 [[0.01322889 0.01359136 0.        ]
  [0.0151036  0.01719316 0.        ]]]
[[[0.01898363 0.02160135 0.        ]
  [0.02086848 0.02596938 0.        ]]

 [[0.01688803 0.02119446 0.        ]
  [0.01858205 0.02557662 0.        ]]]
[[[0.02265458 0.03070028 0.        ]
  [0.02434335 0.03577613 0.        ]]

 [[0.02018562 0.0303208  0.        ]
  [0.02170054 0.03540938 0.        ]]]
[[[0.02593474 0.04117854 0.        ]
  [0.02743158 0.0468908  0.        ]]

 [[0.02312779 0.04082424 0.        ]
  [0.02446936 0.04654855 0.        ]]]
[[[0.02883659 0.05289267 0.        ]
  [0.03015196 0.05916721 0.        ]]

 [[0.0257276

In [17]:
import cv2
import numpy as np
from scipy.interpolate import RBFInterpolator

# Load the image
image = cv2.imread('image.png')
width,height = image.shape[:2]
print(width, height)
w=280
h=259

# Your source points and corresponding destination points
src_points = np.array([
    [0, 0],
    [width,height],
    [width,0],
    [0,height],
])

dst_points = np.array([
    [0, 0],
    [w,h],
    [w,0],
    [0,h],
])

# Create the RBF interpolator instance
rbfx = RBFInterpolator(src_points,dst_points[:,0],kernel="thin_plate_spline")
rbfy = RBFInterpolator(src_points,dst_points[:,1],kernel="thin_plate_spline")

# Create a meshgrid to interpolate over the entire image
img_grid = np.mgrid[0:width, 0:height]

# flatten grid so it could be feed into interpolation
flatten=img_grid.reshape(2, -1).T

# Interpolate the displacement using the RBF interpolators
map_x = rbfx(flatten).reshape(width,height).astype(np.float32)
map_y = rbfy(flatten).reshape(width,height).astype(np.float32)
# Apply the remapping to the image using OpenCV
warped_image = cv2.remap(image, map_y, map_x, cv2.INTER_LINEAR)

# Save or display the result
cv2.imwrite('remap.png', warped_image)



299 259


True